##Importing CSV File for Preprocessing

In [ ]:
import pandas as pd

data = pd.read_csv('final_lematize_translated_data.csv')

##Run all cells before preprocessing

In [ ]:
import nltk
import re
import json
import unicodedata

In [ ]:
!pip install emoji
!pip install demoji

In [ ]:
nltk.download([
...     "names",
...     "stopwords",
...     "state_union",
...     "averaged_perceptron_tagger",
...     "vader_lexicon",
...     "punkt",
        "wordnet",
... ])

[nltk_data] Downloading package names to /root/nltk_data...
[nltk_data]   Unzipping corpora/names.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package state_union to /root/nltk_data...
[nltk_data]   Unzipping corpora/state_union.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [ ]:
from gensim.models import Word2Vec
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from emoji import UNICODE_EMOJI

#PreProcessing Task


###Convert gujarati to english
###Convert all emojis to text
###Convert all text to lower case
###Remove all special characters or links or user tags
###Remove all stopwords
###Lemmatize words



In [ ]:
#Function to remove https and @ tags 
def remove_https_and_tags(data): 

  #Splitting data into words
  data = data.split()

  text = ''
  for word in data:
    
    #If word is not matched add it to string 
    if 'http' in word:
      # print(word)
      continue
    elif 'youtu' in word:
      continue
    else:
      text+=(word + ' ')

  #Removes extra spaces from starting and ending
  text.strip()

  return text

In [ ]:
#Function to convert emoji to text 
import emoji 

# add space near your emoji
def add_space(text):
  result = ''
  for word in emoji.get_emoji_regexp().split(text):
    result+=word
    result+=' '

  return result

def convert_emoji_to_text(data):

  data = data.split()

  #Before converting emojis to text , space is required between word and emoji if there is no space between them
  text = ''
  for word in data:
    text+=(add_space(word) + ' ')
   
  #Removes extra spaces from starting and ending 
  text = text.strip()

  #Now convert emoji to text
  text = emoji.demojize(text, delimiters=("", "")) 
   
  return text

In [ ]:
def remove_special_characters(data):

   #Converting all emojis to respective text
   text = convert_emoji_to_text(data)  

   #Keeping only alpha-numeric and space
   text = re.sub("[^(a-zA-Z \_)]", "", text)

   #Removes extra spaces
   text = re.sub(" +", " ", text)

   #Removing 'https links' and user tags '@*'
   text = remove_https_and_tags(text)

   #Removes spaces from start and end
   text = text.strip()

   #converting data to lower case
   text = text.lower()

   #Keeping only alpha-numeric and space
   text = re.sub("[^(a-zA-Z \_)]", "", text)
  
   return text

In [ ]:
def remove_stopwords(data):
  
  lemmatizer = WordNetLemmatizer()
  data = nltk.word_tokenize(data)
  text = ""
  for word in data:
     if word not in set(stopwords.words('english')):
       word = lemmatizer.lemmatize(word)
       text+= (word + " ")
  text = text.strip()

  return text

#Updating Data Code

##Previous method of converting list item to dictionary just for information

 msg = ast.literal_eval(msg)
      
      #finding first key,value pair
      dict_pairs = msg.items()
      pairs_iterator = iter(dict_pairs)
      first_pair = next(pairs_iterator)
      
      #key is first_pair[0]
      #value is first_pair[1]
      
      if(len(first_pair[1])):
        msg = first_pair[1][0]
        msg = remove_special_characters(msg)
        msg = remove_stopwords(msg)
        
        if(len(msg)):
          dict1 = {}
          list_msg = []
          list_msg.append(msg)
          dict1[first_pair[0]] = list_msg
          subcomment_data.append(dict1)

##Main Code

###Same task are repeated for message,comment,subcomment

##Preprocessing on CSV Data

In [ ]:
import json
import ast
for i in range(data.shape[0]):
# for i in range(4):

  print(i)
  #Message Section
  message = data['post_msg_final'][i]
  
  #Making commas in text as $, so that list can be easily split 
  j=1
  ans="["
  while(j<len(message)-1):
     if(message[j]=='}' and message[j+1]==','):
       ans+="},"
       j+=2
       continue
     if(message[j]==','):
       ans+='$'
     else:
       ans+=message[j]
     j+=1
  ans+="]"
  message = ans
  message = message.strip('][').split(", ")

  message_data = []

  #traversing list
  for msg in message:    
   
    if(len(msg)):

      ans = msg.strip('[{}]')
      
      #Breaking string into 2 parts id, message
      if ':' and '[' in ans:
        ans = ans.split(': [')
      if ':' in ans:
        ans = ans.split(':')
      if '[' in ans:    #this part isn't working 
        ans = ans.split('[')

      #ans[0] - id , ans[1] - message

      #Remving whitespaces from beginning and end from id
    #   print(ans[0])
      if ans!="VALUE":
        if ans[0][1]==' ':
          ans[0] = ans[0][:1]+ans[0][2:]
        if ans[0][-2]==' ':
          ans[0] = ans[0][:-2]+ans[0][-1]
        if(ans[0][18]!='_'):
          ans[0] = ans[0][:18] + '_'+ ans[0][18:]
    
      #If message exists
      if(1<len(ans) and len(ans[1])):
        msg = ans[1]
        msg = remove_special_characters(msg)
        msg = remove_stopwords(msg)

        if(len(msg)):
          dict1 = {}
          list_msg = []
          list_msg.append(msg)
          dict1[ans[0]] = list_msg
          message_data.append(dict1)
  
  # print(message_data)
  data['post_msg_tranlsated_final'][i] = message_data


  #Comments Section
  comments = data['post_comments_final'][i]

  #Modifying string where there is space btw { and ,
  ans1="["
  j=1
  while(j<len(comments)-2):
      if(comments[j]=='}' and comments[j+1]==' ' and comments[j+2]==','):
         ans1+="},"
         j+=3
         continue
      else:
        ans1+=comments[j]
      j+=1
  ans1+=comments[len(comments)-2]
  ans1+="]"
  comments = ans1

  #Making commas in text as $, so that list can be easily split 
  ans="["
  j=1
  while(j<len(comments)-1):
     if(comments[j]=='}' and comments[j+1]==','):
       ans+="},"
       j+=2
       continue
     if(comments[j]==','):
       ans+='$'
     else:
       ans+=comments[j]
     j+=1
  ans+="]"
  comments=ans
  comments = comments.strip('][').split(', ')

  #traversing list
  comment_data = []
  for msg in comments:
    
    if(len(msg)):
      
      ans = msg.strip('[{}]')


      if ':' and '[' in ans:
        ans = ans.split(': [')
      elif ':' in ans:
        ans = ans.split(':')
      elif '[' in ans:
        ans = ans.split('[')
      
    #   print(ans)      #    ---------
      if ans!="VALUE" and len(ans[0]) > 1:
        if ans[0][1]==' ':
          ans[0] = ans[0][:1]+ans[0][2:]
        if ans[0][-2]==' ':
          ans[0] = ans[0][:-2]+ans[0][-1]
    
      if(1<len(ans) and len(ans[1])):

        msg = ans[1]
        msg = remove_special_characters(msg)
        msg = remove_stopwords(msg)

        if(len(msg)):
          dict1 = {}
          list_msg = []
          list_msg.append(msg)
          dict1[ans[0]]=list_msg
          comment_data.append(dict1)


  # print(comment_data)
  data['post_comments_translated_final'][i] = comment_data



  #SubComments Section
  subcomments = data['post_subcomments_final'][i]
  ans1="["
  j=1
  while(j<len(subcomments)-2):
      if(subcomments[j]=='}' and subcomments[j+1]==' ' and subcomments[j+2]==','):
         ans1+="},"
         j+=3
         continue
      else:
        ans1+=subcomments[j]
      j+=1
  ans1+=subcomments[len(subcomments)-2]
  ans1+="]"
  subcomments = ans1
  j=1
  ans="["
  while(j<len(subcomments)-1):
     if(subcomments[j]=='}' and subcomments[j+1]==','):
       ans+="},"
       j+=2
       continue
     if(subcomments[j]==','):
       ans+='$'
     else:
       ans+=subcomments[j]
     j+=1
  ans+="]"
  subcomments = ans
  subcomments = subcomments.strip('][').split(', ')
   
  subcomment_data = []
  for msg in subcomments:

    if(len(msg)):

      ans = msg.strip('[{}]')
      
      if ':' and '[' in ans:
        ans = ans.split(': [')
      if ':' in ans:
        ans = ans.split(':')
      if '[' in ans:
        ans = ans.split('[')

      if ans!="VALUE" and len(ans[0]) > 1:
        if ans[0][1]==' ':
          ans[0] = ans[0][:1]+ans[0][2:]
        if ans[0][-2]==' ':
          ans[0] = ans[0][:-2]+ans[0][-1]

      if(1<len(ans) and len(ans[1])):
        msg = ans[1]
        msg = remove_special_characters(msg)
        msg = remove_stopwords(msg)
        
        if(len(msg)):
          dict1 = {}
          list_msg = []
          list_msg.append(msg)
          dict1[ans[0]] = list_msg
          subcomment_data.append(dict1)

  # print(subcomment_data) 
  data['post_subcomments_translated_final'][i] = subcomment_data


0
1
2
3
4
5
6


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:146: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:21

Streaming output truncated to the last 5000 lines.
13631
13632
13633
13634
13635
13636
13637
13638
13639
13640
13641
13642
13643
13644
13645
13646
13647
13648
13649
13650
13651
13652
13653
13654
13655
13656
13657
13658
13659
13660
13661
13662
13663
13664
13665
13666
13667
13668
13669
13670
13671
13672
13673
13674
13675
13676
13677
13678
13679
13680
13681
13682
13683
13684
13685
13686
13687
13688
13689
13690
13691
13692
13693
13694
13695
13696
13697
13698
13699
13700
13701
13702
13703
13704
13705
13706
13707
13708
13709
13710
13711
13712
13713
13714
13715
13716
13717
13718
13719
13720
13721
13722
13723
13724
13725
13726
13727
13728
13729
13730
13731
13732
13733
13734
13735
13736
13737
13738
13739
13740
13741
13742
13743
13744
13745
13746
13747
13748
13749
13750
13751
13752
13753
13754
13755
13756
13757
13758
13759
13760
13761
13762
13763
13764
13765
13766
13767
13768
13769
13770
13771
13772
13773
13774
13775
13776
13777
13778
13779
13780
13781
13782
13783
13784
13785
13786
13787
13788
1

###Exporting pre-processed data to new file

In [ ]:
data.to_csv('final_lematize_translated_data.csv',index=False)

##Reading preprocessed data columns from CSV File

In [ ]:
import json
import ast

complete_msg= []

for i in range(data.shape[0]):

  print(i)
 
  #Message Section
  message = data['post_msg_tranlsated_final'][i]
  message = message.strip('][').split(", ")

  #traversing list
  for msg in message:    
   
    if(len(msg)):
      
      msg = ast.literal_eval(msg)      

      #finding first key,value pair
      dict_pairs = msg.items()
      pairs_iterator = iter(dict_pairs)
      first_pair = next(pairs_iterator)
    
      #key is first_pair[0]
      #value is first_pair[1]
    
      if(len(dict_pairs) and len(first_pair[1])):
        msg = first_pair[1][0]
        complete_msg.append(msg)
        



  #Comments Section
  comments = data['post_comments_translated_final'][i]
  comments = comments.strip('][').split(", ")

  #traversing list
  for msg in comments:
    
    if(len(msg)):

      msg = ast.literal_eval(msg)  
      #finding first key,value pair
      
      dict_pairs = msg.items()
      pairs_iterator = iter(dict_pairs)
      first_pair = next(pairs_iterator)
    
      #key is first_pair[0]
      #value is first_pair[1]
    
      if(len(dict_pairs) and len(first_pair[1])):
        msg = first_pair[1][0]
        complete_msg.append(msg)



  #SubComments Section
  subcomments = data['post_subcomments_translated_final'][i]
  subcomments = subcomments.strip('][').split(", ")

  for msg in subcomments:

    if(len(msg)):

      msg = ast.literal_eval(msg)  

      #finding first key,value pair
      dict_pairs = msg.items()
      pairs_iterator = iter(dict_pairs)
      first_pair = next(pairs_iterator)
    
      #key is first_pair[0]
      #value is first_pair[1]
    
      if(len(dict_pairs) and len(first_pair[1])):
        msg = first_pair[1][0]
        complete_msg.append(msg)

Streaming output truncated to the last 5000 lines.
13631
13632
13633
13634
13635
13636
13637
13638
13639
13640
13641
13642
13643
13644
13645
13646
13647
13648
13649
13650
13651
13652
13653
13654
13655
13656
13657
13658
13659
13660
13661
13662
13663
13664
13665
13666
13667
13668
13669
13670
13671
13672
13673
13674
13675
13676
13677
13678
13679
13680
13681
13682
13683
13684
13685
13686
13687
13688
13689
13690
13691
13692
13693
13694
13695
13696
13697
13698
13699
13700
13701
13702
13703
13704
13705
13706
13707
13708
13709
13710
13711
13712
13713
13714
13715
13716
13717
13718
13719
13720
13721
13722
13723
13724
13725
13726
13727
13728
13729
13730
13731
13732
13733
13734
13735
13736
13737
13738
13739
13740
13741
13742
13743
13744
13745
13746
13747
13748
13749
13750
13751
13752
13753
13754
13755
13756
13757
13758
13759
13760
13761
13762
13763
13764
13765
13766
13767
13768
13769
13770
13771
13772
13773
13774
13775
13776
13777
13778
13779
13780
13781
13782
13783
13784
13785
13786
13787
13788
1

In [ ]:
sentences = complete_msg
for i in range(len(sentences)):
  print(i)
  sentences[i] = nltk.word_tokenize(sentences[i])
# print(sentences[0])

Streaming output truncated to the last 5000 lines.
97874
97875
97876
97877
97878
97879
97880
97881
97882
97883
97884
97885
97886
97887
97888
97889
97890
97891
97892
97893
97894
97895
97896
97897
97898
97899
97900
97901
97902
97903
97904
97905
97906
97907
97908
97909
97910
97911
97912
97913
97914
97915
97916
97917
97918
97919
97920
97921
97922
97923
97924
97925
97926
97927
97928
97929
97930
97931
97932
97933
97934
97935
97936
97937
97938
97939
97940
97941
97942
97943
97944
97945
97946
97947
97948
97949
97950
97951
97952
97953
97954
97955
97956
97957
97958
97959
97960
97961
97962
97963
97964
97965
97966
97967
97968
97969
97970
97971
97972
97973
97974
97975
97976
97977
97978
97979
97980
97981
97982
97983
97984
97985
97986
97987
97988
97989
97990
97991
97992
97993
97994
97995
97996
97997
97998
97999
98000
98001
98002
98003
98004
98005
98006
98007
98008
98009
98010
98011
98012
98013
98014
98015
98016
98017
98018
98019
98020
98021
98022
98023
98024
98025
98026
98027
98028
98029
98030
98031
9

##Creating Word2vec model for given sentences

In [ ]:
model = Word2Vec(sentences,min_count=2)
words = model.wv.vocab
print(words)

{'cikhalada': <gensim.models.keyedvectors.Vocab object at 0x7f4ff194e8d0>, 'elementary': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1b42b90>, 'school': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1a868d0>, 'monday': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1bb5610>, 'vyara': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1e30410>, 'tafi': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1845fd0>, 'corona': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1845f10>, 'education': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1d11a10>, 'closed': <gensim.models.keyedvectors.Vocab object at 0x7f4ff215bed0>, 'pupil': <gensim.models.keyedvectors.Vocab object at 0x7f4ff192df10>, 'global': <gensim.models.keyedvectors.Vocab object at 0x7f4ffd30dcd0>, 'epidemic': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1d0a6d0>, 'regular': <gensim.models.keyedvectors.Vocab object at 0x7f4ff1b10550>, 'practice': <gensim.models.keyedvectors.Vocab object at 0x7f4ff19ec

##Code for creating and uploading dictionary

In [ ]:
import pandas as pd

data1 = pd.read_csv('word_dictionary.csv')

In [ ]:
word_dict = []
for key,item in words.items():
  temp = []
  temp.append(key)
  temp.append(item)
  word_dict.append(temp)

In [ ]:
colNames = data1.columns

data1_new = pd.DataFrame(data=word_dict, columns=colNames)

# concatenate old and new
df_complete = pd.concat([data1, data1_new], axis = 0)

In [ ]:
df_complete.to_csv('word_dictionary.csv',index=False)

##Code for creating and updating vector

In [ ]:
import pandas as pd

data2 = pd.read_csv('word_vector.csv')

In [ ]:
word_vec = []
for key,item in words.items():
  temp = []
  temp.append(key)
  temp.append(model.wv[key])
  word_vec.append(temp)

In [ ]:
colNames = data2.columns

data2_new = pd.DataFrame(data=word_vec, columns=colNames)

# concatenate old and new
df_complete1 = pd.concat([data2, data2_new], axis = 0)

In [ ]:
df_complete1.to_csv('word_vector.csv',index=False)

##Preprocessing data from text file

In [ ]:
file1 = open('data.txt', 'r')
# file2 = open('lemmatized_data.txt','w')
Lines = file1.readlines()

i=0
complete_data = []
for msg in Lines:
  print(i)
  msg = remove_special_characters(msg)
  msg = remove_stopwords(msg)
  complete_data.append(msg)
  i+=1

file1.close()
# file2.close()
  

Streaming output truncated to the last 5000 lines.
118213
118214
118215
118216
118217
118218
118219
118220
118221
118222
118223
118224
118225
118226
118227
118228
118229
118230
118231
118232
118233
118234
118235
118236
118237
118238
118239
118240
118241
118242
118243
118244
118245
118246
118247
118248
118249
118250
118251
118252
118253
118254
118255
118256
118257
118258
118259
118260
118261
118262
118263
118264
118265
118266
118267
118268
118269
118270
118271
118272
118273
118274
118275
118276
118277
118278
118279
118280
118281
118282
118283
118284
118285
118286
118287
118288
118289
118290
118291
118292
118293
118294
118295
118296
118297
118298
118299
118300
118301
118302
118303
118304
118305
118306
118307
118308
118309
118310
118311
118312
118313
118314
118315
118316
118317
118318
118319
118320
118321
118322
118323
118324
118325
118326
118327
118328
118329
118330
118331
118332
118333
118334
118335
118336
118337
118338
118339
118340
118341
118342
118343
118344
118345
118346
118347
1183

##Tokenising sentence 

In [ ]:
sentences = complete_data
for i in range(len(sentences)):
  print(i)
  sentences[i] = nltk.word_tokenize(sentences[i])
  for word in sentences[i]:
    if len(word)<=3:
      sentences[i].remove(word)
# print(sentences[0])

Streaming output truncated to the last 5000 lines.
118213
118214
118215
118216
118217
118218
118219
118220
118221
118222
118223
118224
118225
118226
118227
118228
118229
118230
118231
118232
118233
118234
118235
118236
118237
118238
118239
118240
118241
118242
118243
118244
118245
118246
118247
118248
118249
118250
118251
118252
118253
118254
118255
118256
118257
118258
118259
118260
118261
118262
118263
118264
118265
118266
118267
118268
118269
118270
118271
118272
118273
118274
118275
118276
118277
118278
118279
118280
118281
118282
118283
118284
118285
118286
118287
118288
118289
118290
118291
118292
118293
118294
118295
118296
118297
118298
118299
118300
118301
118302
118303
118304
118305
118306
118307
118308
118309
118310
118311
118312
118313
118314
118315
118316
118317
118318
118319
118320
118321
118322
118323
118324
118325
118326
118327
118328
118329
118330
118331
118332
118333
118334
118335
118336
118337
118338
118339
118340
118341
118342
118343
118344
118345
118346
118347
1183

##Creating Word2vec Model

In [ ]:
model = Word2Vec(sentences,min_count=1)
words = model.wv.vocab
print(words)

{'cikhalada': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5d09710>, 'elementary': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c47890>, 'school': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c473d0>, 'monday': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c47910>, 'vyara': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c19e90>, 'tafi': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c19d50>, 'corona': <gensim.models.keyedvectors.Vocab object at 0x7f0ead41e690>, 'education': <gensim.models.keyedvectors.Vocab object at 0x7f0ead41e4d0>, 'closed': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c0f850>, 'pupil': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c19e10>, 'global': <gensim.models.keyedvectors.Vocab object at 0x7f0ead41efd0>, 'epidemic': <gensim.models.keyedvectors.Vocab object at 0x7f0ea5c3f5d0>, 'regular': <gensim.models.keyedvectors.Vocab object at 0x7f0ead47c1d0>, 'practice': <gensim.models.keyedvectors.Vocab object at 0x7f0ead47c